# Notebook 3: Injection Generation

In this notebook, we will explore how to generate waveforms with GravyFlow, which can be used to approximate gravitational wave signals. Throughout the GravyFlow library, a significant amount of computation is performed on the GPU. This approach means that there may be some initial overheads compared to CPU calculations, so individual operations might perform more slowly. However, when used for thousands of iterations, GravyFlow methods are often orders of magnitude faster than the functions they were adapted from.

**Note:** As with the previous notebook, the iterators demonstrated in this notebook are not necessarily recommended for use in training machine learning models. Even if you only require waveforms, without any obfuscating noise, it is probably more convenient to use `gf.Dataset`, which will be explained in a later notebook. However, instances of `gf.Dataset` are composed by combining iterators of the type produced in this notebook with iterators shown in subsequent notebooks. Therefore, understanding the function of these iterators is useful.

We will begin by performing the necessary imports:

In [1]:
# Built-in imports
import os
import sys
from typing import Iterator, List, Dict
from pathlib import Path
from itertools import islice

# Dependency imports: 
import numpy as np
import tensorflow as tf
from bokeh.io import show, output_notebook
from bokeh.layouts import gridplot

# GravyFlow import, again adding the grandparent directory to the path:

# Get the absolute path of the grandparent directory (two levels up from the current directory)
parent_dir : Path = os.path.abspath('../../')

# Add the grandparent directory to sys.path if it's not already there.
# This is necessary to import GravyFlow if it's located in the grandparent directory.
if parent_dir not in sys.path:
    sys.path.append(parent_dir)

# Import the GravyFlow module.
import gravyflow as gf

2024-01-17 10:24:23.062364: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-01-17 10:24:24.837258: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


As usual, we will also set up our environment:

**NOTE**: GravyFlow utilizes cuPhenom to generate IMRPhenomD waveforms on the GPU. It's important to note that cuPhenom will attempt to run on the same GPU as GravyFlow. However, cuPhenom does not use memory allocated for TensorFlow by the `gf.Env` function. Therefore, ensure that there is extra GPU memory available if you intend to generate IMRPhenomD waveforms with GravyFlow. This precaution helps in avoiding memory allocation issues and ensures smooth operation.

In [2]:
# Set up the environment using gf.env() and return a tf.distribute.Strategy object.
env : tf.distribute.Strategy = gf.env()

INFO:root:TensorFlow version: 2.12.1, CUDA version: 11.8
2024-01-17 10:24:42.430996: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1635] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 2000 MB memory:  -> device: 0, name: Tesla V100-SXM2-16GB, pci bus id: 0000:85:00.0, compute capability: 7.0
INFO:root:[PhysicalDevice(name='/physical_device:GPU:0', device_type='GPU')]


## Generating Our First Waveform on the GPU

Currently, GravyFlow supports the generation of two waveform types: IMRPhenomD and White Noise Bursts (WNB). It is planned to expand this selection in the future. Both waveform types are generated on the GPU. IMRPhenomD generation utilizes the cuPhenom C library and operates using the CUDA library for GPU processing. On the other hand, WNB generation is integrated within GravyFlow and uses TensorFlow functions.

It's important to note that cuPhenom is designed exclusively for GPU use and does not have CPU support. As such, attempts to run it on a CPU will fail. Additionally, cuPhenom has independent error-checking systems, which may raise errors or cause crashes outside of GravyFlow's control. These errors, often Out Of Memory (OOM) issues, will typically be indicated in the error message. Future enhancements are aimed at more robust integration of cuPhenom errors and improved memory management.

Each waveform type has an associated generator class that inherits from a common parent: gf.WaveformGenerator. This parent has some attributes which are common to all waveform generators, but each waveform generator subclass has extra associated attributes dependent on the parameters of the waveform it is designed to generate. The following attributes are common to all waveform generators:

- `scaling_method`: `Union[gf.ScalingMethod, None]` = `None`
  > This parameter can accept a `gf.ScalingMethod` object, which can be used to scale this waveform when it is injected into obfuscating noise. This process will be discussed in more detail in a later notebook. When the default value, `None`, is used, no scaling will be applied.

- `injection_chance`: `float` = `1.0`
  > This parameter determines how likely it is for the waveform generator to return an injection vs a tensor of all zeros. This functionality is utilized when generating a dataset which contains a mix of examples with and without injected signals. We will also discuss the use of this parameter in more detail in future notebooks. The default value is 1.0, this will cause the iterator to generate injections on every iteration.

- `front_padding_duration_seconds`: `float` = `0.3`
  > GravyFlow Waveform generators output tensors which are the length of the onsource segment duration so that they can be easily summed with obfuscating noise. They will randomize the position of the waveform within that segment between front_padding_duration_seconds and back_padding_duration_seconds. In GravyFlow, injection padding is performed from the last sample of the generated waveform. For example, if front_padding_duration_seconds was 0.3 s, as is default, the last sample of the waveform cannot be less than 0.3 s from the start of the onsource segment. If the waveform is longer than the onsource duration, then the start of the waveform will be cropped and will not appear in the output tensor. If back_padding_duration_seconds was 0.3 s, then the last sample of the generated waveform cannot be within 0.3 s of the end of the onsource segment. If you wish to output waveforms in a fixed position with no random start time variance, set front_padding_duration_seconds = back_padding_duration_seconds = your desired last sample time in seconds. By default, front_padding_duration_seconds is 0.3 s.

- `back_padding_duration_seconds`: `float` = `0.0`
  > This parameter determines the closest the last sample of the generated waveform can be from the end of the onsource period. See the description of front_padding_duration_seconds for more clarification. The default value is 0.0 s, meaning that waveforms can generate up to the end of the onsource window.

- `scale_factor`: `Union[float, None]` = `None`
  > As has been mentioned previously, it is sometimes desirable to scale data to values close to one for easier consumption by artificial neural networks. Rather than using a form of normalization, GravyFlow introduces a scale factor which can be used to scale all waveforms by an identical amount. If None, which is the default, no scaling is performed.

- `network`: `Union[List[IFO], gf.Network, Path, None]` = `None`
  > We can also set the interferometer network configuration we wish to use to project this detector. This is not used by the waveform generator itself, but is used when this is used as part of a composition into a gf.Dataset, which will be described in later datasets. The default value is one.

Let's begin by generating a single IMRPhenomD waveform:

## Generating an IMRPhenomD Waveform

We can create an IMRPhenomD generator by initializing an instance of the `gf.cuPhenomDGenerator` class. This class includes all the parameters of the `gf.WaveformGenerator` class, listed above, along with these extra parameters which determine the properties of the IMRPhenomD waveform:

- `mass_1_msun` : `Union[float, gf.Distribution]` = `30.0`
  > Mass of companion one, in solar masses. The default value is 30.0 solar masses.

- `mass_2_msun` : `Union[float, gf.Distribution]` = `30.0`
  > Mass of companion two, in solar masses. The default value is 30.0 solar masses.

- `inclination_radians` : `Union[float, gf.Distribution]` = `0.0`
  > Inclination of the source in radians. The default is 0.0 radians.

- `distance_mpc` : `Union[float, gf.Distribution]` = `50.0`
  > Distance of the source in megaparsecs. The default value is 50.0 Mpc.

- `reference_orbital_phase_in` : `Union[float, gf.Distribution]` = `0.0`
  > Reference orbital phase in radians. The default is 0.0 radians.

- `ascending_node_longitude` : `Union[float, gf.Distribution]` = `0.0`
  > Longitude of ascending nodes. Degenerate with the polarization angle.

- `eccentricity` : `Union[float, gf.Distribution]` = `0.0`
  > Eccentricity at the reference epoch.

- `mean_periastron_anomaly` : `Union[float, gf.Distribution]` = `0.0`
  > Mean anomaly of periastron.

- `spin_1_in` : `Union[Tuple[float], gf.Distribution]` = `(0.0, 0.0, 0.0)`
  > Dimensionless spin components of the first companion.

- `spin_2_in` : `Union[Tuple[float], gf.Distribution]` = `(0.0, 0.0, 0.0)`
  > Dimensionless spin components of the second companion.

Let us create a PhenomD generator.

In [3]:
# Initialize the PhenomD waveform generator:
# This generator specifically creates IMRPhenomD waveforms based on the given parameters.
phenom_d_generator: gf.WaveformGenerator = gf.cuPhenomDGenerator(
    mass_1_msun=50.0,          # Set the mass of the first companion to 50 solar masses.
    mass_2_msun=50.0,          # Set the mass of the second companion to 50 solar masses.
    inclination_radians=0.0    # Set the inclination of the source to 0 radians.
)

We can use that waveform generator to compose a generic injection generator, which is an instance of `gf.InjectionGenerator`. The reasoning behind this structure will become more apparent as you work with the library.

These are the parameters of `gf.InjectionGenerator`:

- `waveform_generators` : `Union[List[gf.WaveformGenerator], Dict[str, gf.WaveformGenerator]]` : Required
	> List of `gf.WaveformGenerator` instances to use when generating the injection. This is a required input.
- `parameters_to_return` : `Union[List[WaveformParameters], None]` = `None`
	> List of parameters to output for the injection genererator. Default is None, which will return no extra waveform parameters.
- `seed` : `int` = `None`
	> Seed for random number generators used to position injection, generate injection parameters, and generate random elements to some injections like WNBs. Default will revert to see set in gf.Defaults.

Let's create an injection generator with just a `gf.cuPhenomDWaveformGenerator`:

In [4]:
# Create injection generator instance:
phenom_d_injection_generator : gf.InjectionGenerator = gf.InjectionGenerator(phenom_d_generator)

We can use this generator to rapidly generate IMRPhenomD waveforms on the GPU:

In [5]:
# Use the TensorFlow environment 'env' created earlier with gf.env()
with env:
    # Generate batch of IMRPhenomD waveforms, but limit the number of examples in the batch:
    phenom_d_injection, _, _ = next(phenom_d_injection_generator(num_examples_per_batch=1))

2024-01-17 10:24:44.610780: I tensorflow/compiler/xla/service/service.cc:169] XLA service 0x55c87956eef0 initialized for platform CUDA (this does not guarantee that XLA will be used). Devices:
2024-01-17 10:24:44.610825: I tensorflow/compiler/xla/service/service.cc:177]   StreamExecutor device (0): Tesla V100-SXM2-16GB, Compute Capability 7.0
2024-01-17 10:24:44.643222: I tensorflow/compiler/xla/stream_executor/cuda/cuda_dnn.cc:424] Loaded cuDNN version 8600
2024-01-17 10:24:44.664988: I ./tensorflow/compiler/jit/device_compiler.h:180] Compiled cluster using XLA!  This line is logged at most once for the lifetime of the process.


We can plot these using the same plotting helper functions we used in notebook 2. Note that the output of the injection generator is the same size as our onsource duration plus two times our crop duration. This allows for easy addition to any background noise before the whitening process.

In [6]:
# Injection[injection_index][batch_index][polarization_index]
phenom_d_strain_plot = gf.generate_strain_plot(
    {"Plus Polarisation": phenom_d_injection[0][0][0],
     "Cross Polarisation": phenom_d_injection[0][0][1]
    },
    title="Phenom D Injection"
)

# Arrange the plots in a grid layout and display them in the notebook.
output_notebook()
show(phenom_d_strain_plot)

Loading BokehJS ...

## Generating a White Noise Burst (WNB) on the GPU

Similarly, we can generate a White Noise Burst (WNB) on the GPU, using `gf.WNBGenerator` which share the parameters of the `gf.WaveformGenerator` class, but has these additional parameters:

- `duration_seconds` : `Union[float, gf.Distribution]` : = `O.5`
	> The duration of the white noise burst in seconds. Default is 0.5 seconds.
- `min_frequency_hertz` : `Union[float, gf.Distribution]` = `16.0`
	> The minimum frequency component to include when generating the WNB. Default is 16.0 Hertz.
- `max_frequency_hertz` : `Union[float, gf.Distribution]` = `1024.0`
	> The maximum frequency component to include when generating the WNB. Default is 1024.0 Hertz.

Lets create the `gf.WaveformGenerator`:

In [7]:
# Create a WaveformGenerator to generate WNBs:
wnb_generator : gf.WaveformGenerator = gf.WNBGenerator(
    duration_seconds=0.7,
    min_frequency_hertz=16.0,
    max_frequency_hertz=1024.0
)

And the `gf.InjectionGenerator`: 

In [8]:
# Create an injection generator with this waveform generator:
wnb_injection_generator : gf.InjectionGenerator = gf.InjectionGenerator(wnb_generator)

From which we can pull a WNB:

In [10]:
# Use the TensorFlow environment 'env' created earlier with gf.env()
with env:
    # Generate an injection batch with a single WNB injection:
    wnb_injection, _, _ = next(wnb_injection_generator(num_examples_per_batch=1))

2024-01-17 10:24:54.977147: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'num_waveforms' with dtype int32
	 [[{{node num_waveforms}}]]
2024-01-17 10:24:55.104776: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'foldl/while/hann_window/cond/ones/packed/foldl/while/TensorArrayV2Read/TensorListGetItem' with dtype int32
	 [[{{node foldl/while/hann_window/cond/ones/packed/foldl/while/TensorArrayV2Read/TensorListGetItem}}]]


And plot that WNB:

In [28]:
# Injection[injection_index][batch_index][polarization_index]
wnb_strain_plot = gf.generate_strain_plot(
    {"Plus Polarisation": wnb_injection[0][0][0],
     "Cross Polarisation": wnb_injection[0][0][1]
    },
    title="WNB Injection"
)

# Arrange the plots in a grid layout and display them in the notebook.
output_notebook()
show(wnb_strain_plot)

Loading BokehJS ...

## Distributing Parameters

Often, when we are generating datasets to train gravitational wave models, we wish to randomly vary the parameters of the injection with each example produced, GravyFlow allows this functionality with intances of the: `gf.Distribution` class. We use this over any distibution object's from libraries like SciPy and TensorFlow because it allows for discrete and categorical distributions of arbitrary type, which is usefull when they are used for hyperparameter optimisation.

In the next cell we demonstrate `gf.Distributions`:

In [12]:
distribution_examples : Dict = {
	"Constant" : gf.Distribution(value=10, type_=gf.DistributionType.CONSTANT),
	"Uniform" : gf.Distribution(min_=5.0, max_=95.0, type_=gf.DistributionType.UNIFORM),
	"Normal" : gf.Distribution(mean=0.0, std=3.0, type_=gf.DistributionType.NORMAL),
	"Choice" : gf.Distribution(possible_values=["green", "red", "blue"], type_=gf.DistributionType.CHOICE),
	"Log" : gf.Distribution(min_=1.0, max_=10.0, type_=gf.DistributionType.LOG),
	"Powers of two": gf.Distribution(min_=2, max_=1024, type_=gf.DistributionType.POW_TWO, dtype=int)
}

In [18]:
for name, distribution in distribution_examples.items():
	print(f"{name} distribution samples: {distribution.sample(5)}")

Constant distribution samples: [10, 10, 10, 10, 10]
Uniform distribution samples: [30.2344547  23.35219108 61.25582169 63.73438843 85.89267759]
Normal distribution samples: [ 1.14645378 -0.10412185 -2.5596709  -4.39276897 -7.28390815]
Choice distribution samples: ['blue' 'green' 'red' 'green' 'blue']
Log distribution samples: [3.33768594e+03 6.84256779e+02 4.22262164e+06 7.47203406e+06
 1.22819623e+09]
Powers of two distribution samples: [256, 4, 64, 2, 512]


In [19]:
mass_1_distribution_msun : gf.Distribution = gf.Distribution(
    min_=10.0, 
    max_=60.0, 
    type_=gf.DistributionType.UNIFORM
)
mass_2_distribution_msun : gf.Distribution = gf.Distribution(
    min_=10.0, 
    max_=60.0, 
    type_=gf.DistributionType.UNIFORM
)
inclination_distribution_radians: gf.Distribution = gf.Distribution(
    min_=0.0, 
    max_=np.pi, 
    type_=gf.DistributionType.UNIFORM
)

phenom_d_distribution_generator : gf.WaveformGenerator = gf.cuPhenomDGenerator(
    mass_1_msun=mass_1_distribution_msun,
    mass_2_msun=mass_2_distribution_msun,
    inclination_radians=inclination_distribution_radians
)

In [20]:
phenom_d_distribution_injection_generator : gf.InjectionGenerator = gf.InjectionGenerator(
	phenom_d_distribution_generator,
	parameters_to_return = [
		gf.WaveformParameters.MASS_1_MSUN, 
		gf.WaveformParameters.MASS_2_MSUN,
		gf.WaveformParameters.INCLINATION_RADIANS
	]
)

In [21]:
# Use the TensorFlow environment 'env' created earlier with gf.env()
with env:
    phenom_d_distributed_injections, _, phenom_d_distributed_parameters = next(
        phenom_d_distribution_injection_generator(num_examples_per_batch=4)
    )


In [30]:
mass_1_parameters : tf.Tensor = phenom_d_distributed_parameters[gf.WaveformParameters.MASS_1_MSUN]
mass_2_parameters : tf.Tensor = phenom_d_distributed_parameters[gf.WaveformParameters.MASS_2_MSUN]
inclination_parameters : tf.Tensor = phenom_d_distributed_parameters[gf.WaveformParameters.INCLINATION_RADIANS]

distributed_phenom_layout : List = []
for injection, mass_1, mass_2, inclination in zip(
		phenom_d_distributed_injections[0], 
		mass_1_parameters[0], 
		mass_2_parameters[0], 
		inclination_parameters[0]
	):
	distributed_phenom_layout.append([
		gf.generate_strain_plot(
			{
				"Plus Polarisation": injection[0],
				"Cross Polarisation": injection[1]
			},
			height=400,
			title=(
				"Phenom D Injection: \n"
				f"Companion 1 Mass: {mass_1:.2f} solar masses.\n"
				f"Companion 2 Mass: {mass_2:.2f} solar masses.\n"
				f"Inclination: {inclination:.2f} Radians."
			)
		)
	])

# Arrange the plots in a grid layout and display them in the notebook.
grid = gridplot(distributed_phenom_layout)
output_notebook()
show(grid)

Loading BokehJS ...

## Generating Multiple Injections Simultaniously

In [23]:
duration_distribution_seconds : gf.Distribution = gf.Distribution(
    min_=0.1, 
    max_=0.9, 
    type_=gf.DistributionType.UNIFORM
)
min_frequency_distribution_hertz : gf.Distribution = gf.Distribution(
    min_=20.0, 
    max_=512.0, 
    type_=gf.DistributionType.UNIFORM
)
max_frequency_distribution_hertz: gf.Distribution = gf.Distribution(
    min_=20.0, 
    max_=512.0, 
    type_=gf.DistributionType.UNIFORM
)

wnb_distribution_generator : gf.WaveformGenerator = gf.WNBGenerator(
    duration_seconds=duration_distribution_seconds,
    min_frequency_hertz=min_frequency_distribution_hertz,
    max_frequency_hertz=max_frequency_distribution_hertz
)

In [24]:
multi_injection_generator : gf.InjectionGenerator = gf.InjectionGenerator(
	[phenom_d_distribution_generator, wnb_distribution_generator],
	parameters_to_return = [
		gf.WaveformParameters.MASS_1_MSUN, 
		gf.WaveformParameters.MASS_2_MSUN,
		gf.WaveformParameters.INCLINATION_RADIANS,
		gf.WaveformParameters.DURATION_SECONDS, 
		gf.WaveformParameters.MIN_FREQUENCY_HERTZ,
		gf.WaveformParameters.MAX_FREQUENCY_HERTZ,

	]
)

In [25]:
# Use the TensorFlow environment 'env' created earlier with gf.env()
with env:
    multi_injections, _, multi_parameters = next(multi_injection_generator(num_examples_per_batch=4))

2024-01-17 10:26:02.640893: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'num_waveforms' with dtype int32
	 [[{{node num_waveforms}}]]


In [31]:
mass_1_parameters : tf.Tensor = multi_parameters[gf.WaveformParameters.MASS_1_MSUN][0]
mass_2_parameters : tf.Tensor = multi_parameters[gf.WaveformParameters.MASS_2_MSUN][0]
inclination_parameters : tf.Tensor = multi_parameters[gf.WaveformParameters.INCLINATION_RADIANS][0]
duration_parameters : tf.Tensor = multi_parameters[gf.WaveformParameters.DURATION_SECONDS][1]
min_frequency_parameters : tf.Tensor = multi_parameters[gf.WaveformParameters.MIN_FREQUENCY_HERTZ][1]
max_frequency_parameters : tf.Tensor = multi_parameters[gf.WaveformParameters.MAX_FREQUENCY_HERTZ][1]

distributed_phenom_layout : List = []
for phenom_d_injections, wnb_injections, mass_1, mass_2, inclination, duration, min_freq, max_freq in zip(
		multi_injections[0], 
		multi_injections[1],
		mass_1_parameters, 
		mass_2_parameters, 
		inclination_parameters,
		duration_parameters,
		min_frequency_parameters,
		max_frequency_parameters
	):
	distributed_phenom_layout.append([
		gf.generate_strain_plot(
			{
				"Plus Polarisation": phenom_d_injections[0],
				"Cross Polarisation": phenom_d_injections[1]
			},
			height=400,
			width=500,
			title=(
				"Phenom D Injection:\n"
				f"Companion 1 Mass: {mass_1:.2f} solar masses.\n"
				f"Companion 2 Mass: {mass_2:.2f} solar masses.\n"
				f"Inclination: {inclination:.2f} Radians."
			)
		),
		gf.generate_strain_plot(
			{
				"Plus Polarisation": wnb_injections[0],
				"Cross Polarisation": wnb_injections[1]
			},
			height=400,
			width=500,
			title=(
				"WNB Injection:\n"
				f"Duration: {duration:.2f} s.\n"
				f"Minimum Frequency: {min_freq:.2f} Hz.\n"
				f"Maximum Frequency: {max_freq:.2f} Hz."
			)
		)
	])

# Arrange the plots in a grid layout and display them in the notebook.
grid = gridplot(distributed_phenom_layout)
output_notebook()
show(grid)

Loading BokehJS ...

## Loading Injections from Config JSON


## Varying Injection Chance